## Robust Multi-Circle Tracking with Occlusion Handling

To detect, track, and assign consistent IDs to up to 10 visually distinct circles in a video across frames, even under partial occlusions, fast movements, or visual noise - ensuring all detected circles are:

*   Drawn accurately with a bounding perimeter and black center
*   Assigned unique, persistent IDs from 1 to 10
*   Logged in a CSV file with center coordinates and radius









In [16]:
# Step 1: Upload video
from google.colab import files
uploaded = files.upload()

# Step 2: Import libraries
import cv2  # OpenCV for video processing
import numpy as np  # Numerical computations
import pandas as pd  # Data manipulation
from IPython.display import HTML, display  # For displaying HTML/video in notebook
from base64 import b64encode  # Encode video for inline display
from scipy.optimize import linear_sum_assignment  # Hungarian algorithm for assignment
import IPython

Saving Dot_Track_Vid_AU.mp4 to Dot_Track_Vid_AU.mp4


### Improved Edge Detection Robustness
the first look at the video tells that detecting edges first wherever there is a colour hange will help in detecting bubbles later. Hence, Canny edge detection is applied and further enhanced with CIELAB using horizontal and vertical color difference.
*   Fine-tuned thresholds(10.8 LAB diff) for better edge detection.
*   Applied morphological closing to fill broken circle edges.


In [18]:
# Load video and extract basic properties
video_path = next(iter(uploaded))  # Get uploaded video path
cap = cv2.VideoCapture(video_path)  # Open video file
fps = int(cap.get(cv2.CAP_PROP_FPS))  # Frames per second
width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))  # Frame width
height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))  # Frame height

# Initialize video writer for saving processed output
out = cv2.VideoWriter("edge_detection_output.mp4", cv2.VideoWriter_fourcc(*'mp4v'), fps, (width, height))

# Process each frame in the video
while True:
    ret, frame = cap.read()  # Read next frame
    if not ret:
        break  # Stop if no more frames

    # Apply preprocessing: smoothing and contrast enhancement
    blurred = cv2.medianBlur(frame, 5)  # Reduce noise using median blur
    gray = cv2.cvtColor(blurred, cv2.COLOR_BGR2GRAY)  # Convert to grayscale
    gray = cv2.createCLAHE(clipLimit=3.0, tileGridSize=(8, 8)).apply(gray)  # Enhance contrast using CLAHE

    # Canny edge detection
    edges_canny = cv2.Canny(gray, 30, 150)

    # LAB color edge detection based on color differences
    lab = cv2.cvtColor(blurred, cv2.COLOR_BGR2LAB).astype(np.float32)
    diff_x = np.linalg.norm(lab[:, 1:] - lab[:, :-1], axis=2)  # Horizontal color diff
    diff_y = np.linalg.norm(lab[1:, :] - lab[:-1, :], axis=2)  # Vertical color diff

    # Threshold differences to create edge masks
    edge_x = (diff_x > 10.7).astype(np.uint8) * 255
    edge_y = (diff_y > 10.7).astype(np.uint8) * 255

    # Combine LAB-based edge masks
    edge_lab = np.zeros((frame.shape[0], frame.shape[1]), dtype=np.uint8)
    edge_lab[:, 1:] = np.maximum(edge_lab[:, 1:], edge_x)
    edge_lab[1:, :] = np.maximum(edge_lab[1:, :], edge_y)

    # Combine Canny and LAB edges
    combined_edges = cv2.bitwise_or(edges_canny, edge_lab)

    # Enhance edges using morphological operations
    kernel = cv2.getStructuringElement(cv2.MORPH_ELLIPSE, (5, 5))
    combined_edges = cv2.morphologyEx(combined_edges, cv2.MORPH_CLOSE, kernel)  # Fill gaps in edges
    combined_edges = cv2.dilate(combined_edges, None)  # Make edges thicker

    # Draw detected edges in red over the original frame
    output = frame.copy()
    output[combined_edges > 0] = [0, 0, 255]  # Set edge pixels to red
    out.write(output)  # Write to output video

# Release video readers and writers
cap.release()
out.release()

# Convert and display final video with compression
!ffmpeg -i edge_detection_output.mp4 -vcodec libx264 -crf 23 edge_detection_display.mp4 -y -loglevel quiet
mp4 = open("edge_detection_display.mp4", 'rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML(f"""
<video width=640 controls>
  <source src="{data_url}" type="video/mp4">
</video>
""")


The output above shows near perfect edge detections which will be helpful to any algorithm for detecting different shapes in the video.

### Applied Hough Circle Transform to detect circular blobs using:

*  HoughCircles detects circles by distinguishing between straight lines and curves like arcs and full curcles, with calibrated parameters: param1, param2, minRadius, maxRadius.
* Carefully finetuned the prameters to detect as many circles as possible.






In [29]:
# Step 3: Load video
video_path = next(iter(uploaded))
cap = cv2.VideoCapture(video_path)
fps = int(cap.get(cv2.CAP_PROP_FPS))
width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
total_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))  # Total number of frames

# Output video writer
out_path = "Bubble_detection_output.mp4"
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
out = cv2.VideoWriter(out_path, fourcc, fps, (width, height))

# Counters and storage for analysis
total_detected_circles = 0       # All visually detected circles (via Hough)
total_blue_circles = 0           # Circles actually drawn on frame with blue border
all_detected_data = []           # To store CSV output: Frame, X, Y, Radius

# Main frame loop
frame_idx = 0
while True:
    ret, frame = cap.read()
    if not ret:
        break

    # Preprocess frame
    blurred = cv2.medianBlur(frame, 5)
    gray = cv2.cvtColor(blurred, cv2.COLOR_BGR2GRAY)
    gray = cv2.createCLAHE(clipLimit=3.0, tileGridSize=(8,8)).apply(gray)  # Improve contrast

    # Detect circles using Hough Transform
    output = frame.copy()
    circles = cv2.HoughCircles(gray, cv2.HOUGH_GRADIENT, 1.08, 45,
                               param1=50, param2=27.5,
                               minRadius=20, maxRadius=120)

    # Step 9: Draw and record all detected circles
    if circles is not None:
        circles = np.round(circles[0, :]).astype(int)
        total_detected_circles += len(circles)

        for (x, y, r) in circles:
            # Draw every detected circle with a blue outline (no ID, no radius)
            cv2.circle(output, (x, y), r, (255, 0, 0), 2)
            cv2.circle(output, (x, y), 2, (0, 0, 0), -1)
            total_blue_circles += 1
            all_detected_data.append([frame_idx, x, y, r])  # Save to CSV

    # Write output frame
    out.write(output)
    frame_idx += 1

# Finalize video and save results
cap.release()
out.release()

# Save CSV with detected circle info
df = pd.DataFrame(all_detected_data, columns=["Frame", "X", "Y", "Radius"])
df.to_csv("detected_bubbles_output.csv", index=False)

# Calculate and print performance score
expected_circles = total_frames * 10
performance_score = total_detected_circles / expected_circles

print(f"Total frames: {total_frames}")
print(f"Total detected bubbles (via Hough): {total_detected_circles}")
print(f"Detection Coverage: {total_detected_circles}/{expected_circles} ({performance_score:.2%})")

# Display video inline
!ffmpeg -i Bubble_detection_output.mp4 -vcodec libx264 -crf 23 Bubble_detection_display.mp4 -y -loglevel quiet
mp4 = open("Bubble_detection_display.mp4", 'rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()

HTML(f"""
<video width=640 controls>
  <source src="{data_url}" type="video/mp4">
</video>
""")


Total frames: 153
Total detected bubbles (via Hough): 1339
Detection Coverage: 1339/1530 (87.52%)


We know that there are 10 circles in each frame and ther are 153 total frames captured int he video. ideally there must be 1530 circles that must be detected, 10 circles in each frame. Hough circles worked well for well-defined circles, detecting 87% of circles in each frame on average, including <10 false positives and rest missed some due to small arcs and hidden behind other objects.

### Tracking with Hungarian Algorithm
First used Hungarian Algorithm (Linear Sum Assignment) for circle matching:



*   Matched detected circles to previous frame’s IDs based on a cost matrix.
*   Minimzed cost based on difference in radius and Euclidean distance between centers of previous and current frame giving 80% eight to radius match.

Cost = 0.8 * radius_diff+0.2 * Euclidean_distance

### Radius-Aware and ID-Constrained Tracking
* Calculated moving average radius for each circle ID using a 10-frame window.

* Applied a dynamic radius tolerance: 10% of the moving average.

* Kept the ID assignment limited to 1–10.











In [31]:
# Load input video and set up capture parameters
video_path = next(iter(uploaded))
cap = cv2.VideoCapture(video_path)
fps = int(cap.get(cv2.CAP_PROP_FPS))
width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
total_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))

# Set up video writer to save output with tracking overlay
out = cv2.VideoWriter("Bubble_tracking_output.mp4",
                      cv2.VideoWriter_fourcc(*'mp4v'),
                      fps, (width, height))

# Initialize tracking state
tracked_circles = []                   # Stores tracking info per frame
reference_history, reference_position = {}, {}  # Tracks radius history and last known positions
missing_circles, frame_detected_counts = {}, []
total_blue_drawn = 0                   # Debug count of how many circles were tracked visually

# Parameters
history_len = 10                       # Number of past frames to consider for smoothing
max_dist_threshold = 500              # Cost threshold for valid matches
radius_tolerance_ratio = 0.1          # Allowed deviation in radius
frame_idx = 0

# Start frame-by-frame processing
while True:
    ret, frame = cap.read()
    if not ret:
        break

    # Apply median blur and histogram equalization to enhance circle detection
    blurred = cv2.medianBlur(frame, 5)
    gray = cv2.cvtColor(blurred, cv2.COLOR_BGR2GRAY)
    gray = cv2.createCLAHE(clipLimit=3.0, tileGridSize=(8,8)).apply(gray)

    # Detect circles using Hough Circle Transform
    output = frame.copy()
    circles = cv2.HoughCircles(gray, cv2.HOUGH_GRADIENT, 1.08, 45,
                               param1=50, param2=27.5,
                               minRadius=20, maxRadius=120)

    matched_ids, count_in_frame = set(), 0

    if circles is not None:
        circles = np.round(circles[0, :]).astype(int)
        detected = [(x, y, r) for (x, y, r) in circles]
        count_in_frame = len(detected)
        frame_ids_used = set()

        if frame_idx == 0:
            # Assign initial IDs based on sorted radius for first frame
            for i, (x, y, r) in enumerate(sorted(detected, key=lambda x: (x[2], x[0], x[1]))[:10]):
                reference_history[i+1] = [r]
                reference_position[i+1] = (x, y)
                # Draw circle and ID label
                cv2.circle(output, (x, y), r, (255, 0, 0), 2)
                cv2.circle(output, (x, y), 2, (0, 0, 0), -1)
                cv2.putText(output, str(i+1), (x - 15, y - 15), cv2.FONT_HERSHEY_SIMPLEX, 0.6, (0, 0, 0), 2)
                tracked_circles.append([frame_idx, i + 1, x, y, r])
                total_blue_drawn += 1
        else:
            # Build cost matrix between last known positions and current detections
            prev_data = [(rid, *reference_position[rid], np.mean(reference_history[rid][-history_len:]))
                         for rid in reference_history]
            cost_matrix = np.full((len(prev_data), len(detected)), 1e6)

            for i, (rid, px, py, pr) in enumerate(prev_data):
                radius_tolerance = max(6, radius_tolerance_ratio * pr)
                for j, (x, y, r) in enumerate(detected):
                    if abs(r - pr) < radius_tolerance:
                        dist = np.linalg.norm([px - x, py - y])
                        cost_matrix[i, j] = 0.9 * abs(r - pr) + 0.1 * dist

            # Use Hungarian algorithm to assign detections to existing IDs
            row_ind, col_ind = linear_sum_assignment(cost_matrix)

            for i, j in zip(row_ind, col_ind):
                if cost_matrix[i, j] < max_dist_threshold:
                    rid = prev_data[i][0]
                    x, y, r = detected[j]
                    if rid not in frame_ids_used:
                        # Update tracking state
                        reference_history[rid].append(r)
                        reference_history[rid] = reference_history[rid][-history_len:]
                        reference_position[rid] = (x, y)
                        missing_circles[rid] = 0
                        # Draw tracking overlay
                        cv2.circle(output, (x, y), r, (255, 0, 0), 2)
                        cv2.circle(output, (x, y), 2, (0, 0, 0), -1)
                        cv2.putText(output, str(rid), (x - 15, y - 15), cv2.FONT_HERSHEY_SIMPLEX, 0.8, (0, 0, 0), 2)
                        tracked_circles.append([frame_idx, rid, x, y, r])
                        frame_ids_used.add(rid)
                        total_blue_drawn += 1

    # Update missing frame counts for each ID
    for rid in reference_history:
        if rid in reference_position and rid not in matched_ids:
            missing_circles[rid] = missing_circles.get(rid, 0) + 1
        else:
            missing_circles[rid] = 0

    frame_detected_counts.append(count_in_frame)
    out.write(output)
    frame_idx += 1

# Release video objects
cap.release()
out.release()

# Save tracking results to CSV
pd.DataFrame(tracked_circles, columns=["Frame", "ID", "X", "Y", "Radius"]).to_csv("detected_circles_output.csv", index=False)

# Summary statistics
print(f"Total circles detected: {len(tracked_circles)} / {total_frames * 10}")
print(f"Detection coverage: {100 * len(tracked_circles) / (total_frames * 10):.2f}%")

# Convert output video to displayable format and embed in notebook
!ffmpeg -i Bubble_tracking_output.mp4 -vcodec libx264 -crf 23 Bubble_tracking_display.mp4 -y -loglevel quiet
mp4 = open("Bubble_tracking_display.mp4", 'rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML(f"""
<video width=640 controls>
  <source src="{data_url}" type="video/mp4">
</video>
""")


Total circles detected: 1315 / 1530
Detection coverage: 85.95%


The output video above shows tracking of 86% of bubbles after removing the false positives. After taking a closer look at the CSV file of radius and center coordinates of detected circles, i observed:
 * Position of the circles is not known/detected for a few frames which can be imputed assuming a linear motion between last and next known location of the circles.
 * Radius is imputed using the average across all frames and center coordinates are impured using linear interpolation. imputed circles are drawn with red line for seperation.

In [35]:
# Load video using OpenCV
video_path = next(iter(uploaded))  # Get uploaded video path
cap = cv2.VideoCapture(video_path)
fps = int(cap.get(cv2.CAP_PROP_FPS))  # Frames per second
width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))  # Frame width
height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))  # Frame height
total_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))  # Total number of frames in video

# Initialize video writer for output
out = cv2.VideoWriter("Final_bubble_tracking_output.mp4",
                      cv2.VideoWriter_fourcc(*'mp4v'),
                      fps, (width, height))

# Initialize tracking state and counters
tracked_circles, reference_history, reference_position = [], {}, {}
missing_circles, frame_detected_counts = {}, []
total_blue_drawn = 0

# Parameters for tracking
history_len = 10  # Number of frames to consider for radius smoothing
max_dist_threshold = 500  # Maximum allowed distance for matching detections
radius_tolerance_ratio = 0.05  # Tolerance for radius change
max_missing_frames = 8  # Frames after which a circle is considered lost
frame_idx = 0  # Current frame index

# Read frames one-by-one
while True:
    ret, frame = cap.read()
    if not ret:
        break

    # Preprocess frame
    blurred = cv2.medianBlur(frame, 5)
    gray = cv2.cvtColor(blurred, cv2.COLOR_BGR2GRAY)
    gray = cv2.createCLAHE(clipLimit=3.0, tileGridSize=(8,8)).apply(gray)  # Improve contrast

    # Detect circles using Hough Transform
    output = frame.copy()
    circles = cv2.HoughCircles(gray, cv2.HOUGH_GRADIENT, 1.08, 45,
                               param1=50, param2=27.5,
                               minRadius=20, maxRadius=120)

    matched_ids, count_in_frame = set(), 0

    if circles is not None:
        circles = np.round(circles[0, :]).astype(int)
        count_in_frame = len(circles)
        detected = [(x, y, r) for (x, y, r) in circles]
        frame_ids_used = set()

        if frame_idx == 0:
            # Initialize first frame with top 10 largest circles
            for i, (x, y, r) in enumerate(sorted(detected, key=lambda x: (x[2], x[0], x[1]))[:10]):
                reference_history[i+1] = [r]
                reference_position[i+1] = (x, y)
                tracked_circles.append([frame_idx, i + 1, x, y, r])
        else:
            # Match current frame detections to reference positions using cost matrix
            prev_data = [(rid, *reference_position[rid], np.mean(reference_history[rid][-history_len:]))
                         for rid in reference_history]
            cost_matrix = np.full((len(prev_data), len(detected)), 1e6)

            for i, (rid, px, py, pr) in enumerate(prev_data):
                radius_tolerance = max(6, radius_tolerance_ratio * pr)
                for j, (x, y, r) in enumerate(detected):
                    if abs(r - pr) < radius_tolerance:
                        dist = np.linalg.norm([px - x, py - y])
                        cost_matrix[i, j] = 0.9 * abs(r - pr) + 0.1 * dist

            # Assign using Hungarian algorithm
            row_ind, col_ind = linear_sum_assignment(cost_matrix)
            assigned_detections = set()

            for i, j in zip(row_ind, col_ind):
                if cost_matrix[i, j] < max_dist_threshold:
                    rid = prev_data[i][0]
                    x, y, r = detected[j]
                    if rid not in frame_ids_used:
                        reference_history[rid].append(r)
                        reference_history[rid] = reference_history[rid][-history_len:]
                        reference_position[rid] = (x, y)
                        missing_circles[rid] = 0
                        tracked_circles.append([frame_idx, rid, x, y, r])
                        assigned_detections.add(j)
                        frame_ids_used.add(rid)

    # Update missing count
    for rid in reference_history:
        if rid in reference_position and rid not in matched_ids:
            missing_circles[rid] = missing_circles.get(rid, 0) + 1
        else:
            missing_circles[rid] = 0

    frame_detected_counts.append(count_in_frame)
    frame_idx += 1

cap.release()

# Save raw tracking results
raw_df = pd.DataFrame(tracked_circles, columns=["Frame", "ID", "X", "Y", "Radius"])
raw_df.to_csv("Pre_imput_bubble_tracking_output.csv", index=False)

# Pivot data into ID × Frame matrices for imputation
x_pivot = raw_df.pivot(index="Frame", columns="ID", values="X")
y_pivot = raw_df.pivot(index="Frame", columns="ID", values="Y")
r_pivot = raw_df.pivot(index="Frame", columns="ID", values="Radius")

# Create a mask for values we want to skip imputation (if movement is too large)
def mask_by_distance(x_pivot, y_pivot, max_dist=200):
    mask = x_pivot.isna() | y_pivot.isna()
    for col in x_pivot.columns:
        x_series = x_pivot[col].copy()
        y_series = y_pivot[col].copy()
        for i in range(1, len(x_series) - 1):
            if pd.isna(x_series.iloc[i]) or pd.isna(y_series.iloc[i]):
                prev_idx = x_series[:i].last_valid_index()
                next_idx = x_series[i+1:].first_valid_index()
                if prev_idx is not None and next_idx is not None:
                    dx = x_series.loc[next_idx] - x_series.loc[prev_idx]
                    dy = y_series.loc[next_idx] - y_series.loc[prev_idx]
                    dist = np.sqrt(dx**2 + dy**2)
                    if dist >= max_dist:
                        mask.iloc[i, x_pivot.columns.get_loc(col)] = True
    return mask

# Apply mask to ignore long jumps
distance_mask = mask_by_distance(x_pivot, y_pivot, max_dist=400)
x_pivot = x_pivot.mask(distance_mask)
y_pivot = y_pivot.mask(distance_mask)

# Interpolate missing values with linear interpolation
x_interp = x_pivot.interpolate(method='linear', axis=0).bfill().ffill().round().astype(int)
y_interp = y_pivot.interpolate(method='linear', axis=0).bfill().ffill().round().astype(int)
r_interp = r_pivot.fillna(r_pivot.mean()).round().astype(int)  # Fill radius with average

# Convert wide (pivoted) format back to long format for rendering
df_imputed = pd.DataFrame({
    'Frame': np.repeat(x_interp.index.values, x_interp.shape[1]),
    'ID': np.tile(x_interp.columns.values, x_interp.shape[0]),
    'X': x_interp.values.flatten(),
    'Y': y_interp.values.flatten(),
    'Radius': r_interp.values.flatten()
})

# Redraw all circles onto video
cap = cv2.VideoCapture(video_path)
out_final = cv2.VideoWriter("Final_bubble_tracking_output.mp4",
                            cv2.VideoWriter_fourcc(*'mp4v'),
                            fps, (width, height))

frame_idx = 0
while True:
    ret, frame = cap.read()
    if not ret or frame_idx > df_imputed['Frame'].max():
        break

    output = frame.copy()
    for row in df_imputed[df_imputed['Frame'] == frame_idx].itertuples():
        x, y, r, rid = int(row.X), int(row.Y), int(row.Radius), int(row.ID)
        original_row = raw_df[(raw_df['Frame'] == frame_idx) & (raw_df['ID'] == rid)]
        is_imputed = original_row[['X', 'Y']].isna().any(axis=1).any() if not original_row.empty else True
        color = (0, 0, 255) if is_imputed else (255, 0, 0)  # Red if imputed, Blue otherwise
        cv2.circle(output, (x, y), r, color, 2)
        cv2.circle(output, (x, y), 2, (0, 0, 0), -1)
        cv2.putText(output, str(rid), (x - 20, y - 20), cv2.FONT_HERSHEY_SIMPLEX, 0.8, (0, 0, 0), 2)

    out_final.write(output)
    frame_idx += 1

cap.release()
out_final.release()

# Create pivot table with (x, y) coordinates as string for each ID and Frame
coord_pivot = df_imputed.copy()
coord_pivot["Coordinates"] = coord_pivot.apply(lambda row: f"({row.X}, {row.Y})", axis=1)

# Pivot: rows = Frame, columns = ID, values = Coordinates
pivot_coords = coord_pivot.pivot(index="Frame", columns="ID", values="Coordinates")

# Save to CSV
pivot_coords.to_csv("Final_bubble_tracking_coordinates.csv", index=False)

# Save imputed output
df_imputed.reset_index().to_csv("Final_bubble_tracking_output.csv", index=False)

# Stats
total_tracked = len(df_imputed)
total_detected = len(raw_df)
print(f"Total circles detected: {total_detected} / {total_frames * 10}")
print(f"Detection coverage: {100 * total_detected / (total_frames * 10):.2f}%")


# Convert output video to displayable format and embed in notebook
!ffmpeg -i Final_bubble_tracking_output.mp4 -vcodec libx264 -crf 23 Final_bubble_tracking_display.mp4 -y -loglevel quiet
mp4 = open("Final_bubble_tracking_display.mp4", 'rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML(f"""
<video width=640 controls>
  <source src="{data_url}" type="video/mp4">
</video>
""")


Total circles detected: 1315 / 1530
Detection coverage: 85.95%


The above output is the final output which tracks 86% of bubbles on average highlighted in blue in the entire video and rest all highlighted in red are predicted using mean and linear interpolation imputation techiques



Limitations:

* Some circles are not being detected visually even though they are partially visible.
* Linear interpolation assumes straight travel path which might not show some red circles at the exact position, though with same radius and ID.
* Some circles, especially 3,4,5, have similar radius and are observed to swtich IDs in a few frames.

Further improvements:

* More precise prameter tuning to detect even smallest arcs as a circle.
* Kalman filter to enhance motion tracking.
* Color based identificaiton to address ID switching between circles of similar size.

---

References:
* http://vision.stanford.edu/teaching/cs131_fall1718/files/cs131-class-notes.pdf
* Bewley, A., Ge, Z., Ott, L., Ramos, F., & Upcroft, B. (2016). *Simple online and realtime tracking.* IEEE International Conference on Image Processing (ICIP). DOI: [10.1109/ICIP.2016.7533003](https://doi.org/10.1109/ICIP.2016.7533003)

* Canny, J. (1986). *A computational approach to edge detection.* IEEE Transactions on Pattern Analysis and Machine Intelligence, PAMI-8(6), 679–698 DOI: [10.1109/TPAMI.1986.4767851](https://doi.org/10.1109/TPAMI.1986.4767851)

* Duda, R. O., & Hart, P. E. (1972). *Use of the Hough transformation to detect lines and curves in pictures.* Communications of the ACM, 15(1), 11–15. DOI: [10.1145/361237.361242](https://doi.org/10.1145/361237.361242)

* OpenAI. (2024). ChatGPT (June 2025 version) [Large language model]. https://chat.openai.com

* Kuhn, H. W. (1955). *The Hungarian method for the assignment problem.* Naval Research Logistics Quarterly, 2(1‐2), 83–97. DOI: [10.1002/nav.3800020109](https://doi.org/10.1002/nav.3800020109)

* Sharma, G. & Trussell, H. J. (1997). *Digital color imaging.* IEEE Transactions on Image Processing, 6(7), 901–932. DOI: [10.1109/83.585269](https://doi.org/10.1109/83.585269)

* Wang, Y., Xu, Y., & Yuille, A. L. (2017). *DeepFlow: Large displacement optical flow with deep matching.* IEEE International Conference on Computer Vision (ICCV) DOI: [10.1109/TPAMI.2014.2343963](https://doi.org/10.1109/TPAMI.2014.2343963)
